In [1]:
import uproot, awkward
import matplotlib.pyplot as plt
from matplotlib import cm
from matplotlib.colors import ListedColormap, LinearSegmentedColormap, LogNorm
import numpy as np
import pandas as pd
from scipy.signal import find_peaks
import plotly.graph_objects as go
import plotly.express as px
from astropy.modeling import models, fitting
import pickle

In [2]:
file = uproot.open("../rootfiles/cal01.root")

In [3]:
tree = file['calibration1']

Define a nice cmp for any 2D hists we want later:

In [4]:
Greys = cm.get_cmap('Greys', 256)
newcolors = Greys(np.linspace(0, 1, 256))
white = np.array([1, 1, 1, 0])
black = np.array([0, 0, 0, 1])
newcolors[:1, :] = white
newcolors[1:, :] = black
newcmpBlack = ListedColormap(newcolors)

In the next cell, take the tree and put all the branches into a data frame, correctly labeled by strip number.

In [5]:
brancharr = []
detnames = ["U1", "D1", "R1", "L1", "U2", "D2", "R2", "L2"]
df = pd.DataFrame()

chanlast = 0
for adcnum in range(6):
    adcnum = adcnum + 8
    #print("adc: " + str(adcnum))
    if adcnum < 10:
        endname = "_adc0"
    else:
        endname = "_adc"
    if adcnum < 13:
        for chnum in range(32):
            chan = chnum + 1 + chanlast
            if chan < 10:
                startname = "b00"
            elif chan < 100:
                startname = "b0"
            else:
                startname = "b"
            branchname = startname + str(chan) + endname + str(adcnum)
            
            brancharr.append(branchname)
    if adcnum == 13:
        for chan in range(2):
            chan = chan + 1 + chanlast
            branchname = "b" + str(chan) + "_adc" + str(adcnum)
            brancharr.append(branchname)
    chanlast = chan

#print(brancharr)
for i in range(len(brancharr)):
    branch = brancharr[i]
    if i < 32:
        if i < 16:
            df["U1_" + str(i) + "_O"] = tree.array(branch)
        if i > 15:
            df["U1_" + str(i-16) + "_I"] = tree.array(branch)
    elif 31 < i < 64:
        if i-32 < 16:
            df["D1_" + str(i-32) + "_O"] = tree.array(branch)
        if i-32 > 15:
            df["D1_" + str(i-32-16) + "_I"] = tree.array(branch)
    elif 63 < i < 96:
        if i-64 < 16:
            df["R1_" + str(i-64) + "_O"] = tree.array(branch)
        if i-64 > 15:
            df["R1_" + str(i-64-16) + "_I"] = tree.array(branch)
    elif 95 < i < 128:
        if i-96 < 16:
            df["L1_" + str(i-96) + "_O"] = tree.array(branch)
        if i-96 > 15:
            df["L1_" + str(i-96-16) + "_I"] = tree.array(branch)
    elif 127 < i < 144:
        df["U2_" + str(i-128)] = tree.array(branch)
    elif 143 < i < 160:
        df["D2_" + str(i-144)] = tree.array(branch)
    elif i == 160:
        df["R2_0"] = tree.array(branch)
    elif i == 161:
        df["L2_0"] = tree.array(branch)

In [6]:
#fig, axs = plt.subplots()
#axs.hist2d(df["U1_0_I"]*.95861, df["U1_0_O"], cmap=newcmpBlack, bins=(1900,1900), range=[[0,1900],[0,1900]])

Below is a general outline of how we're going to fit each spectrum to calibrate:

1. First, we need to histogram each det/strip using cnts, binedges = np.histogram(detstrip, 500, range=(0,4000))
2. Next, we need to get the bin centers (binc) by averaging each bin edge.
3. Now, we need to find the peak in the spectrum. Use peaks, _ = find_peaks(cnts, height=1000). The entries in peaks are the array index, so to get the bin of the peak, do peak = binc[peaks]. Generally, we'll take the highest peak because it'll probably be close enough for most. 
4. Use astropy to fit a gaussian to the spectrum, need to have guesses to start the fit.:
>g_init = models.Gaussian1D(amplitude=5000, mean=peak, stddev=50)  
>fit_g = fitting.LevMarLSQFitter()  
>g = fit_g(g_init, binc, cnts)  

In [7]:
#gaindet[det, strip, num]
detnames = ["U2", "D2", "R2", "L2"]

In [46]:
ecalE = []

for det in range(4):
    ecalE.append([])
    if det == 0 or det == 1:
        numstrips = 16
    else:
        numstrips = 1
    for strip in range(numstrips): 
        cnts, binedges = np.histogram(df[detnames[det] + "_" + str(strip)], 500, range=(0,4000))
        binc = []
        for i in range(len(binedges)-1):
            binc.append((binedges[i]+binedges[i+1])/2)

        # For the height, use 80% of the highest bin, chopping off the first hundred bins, since the max should occur after:
        peaks, _ = find_peaks(cnts, height=np.amax(cnts[10:])*.8)
        if len(peaks) > 0:
            peak = peaks[len(peaks)-1]
            peakpos = binc[peak]
        else: peakpos = 0
  
        g_init = models.Gaussian1D(amplitude=10000, mean=peakpos, stddev=50)
        fit_g = fitting.LevMarLSQFitter()
        g = fit_g(g_init, binc, cnts)

        # Source produced a line at 5.8 MeV
        ecalE[det].append(5.80/g.mean.value)

Now that we have all of the calibration slopes, we can apply them to each strip and new columns onto the data frame.

In [50]:
for det in range(4):
    if det == 0 or det == 1:
        numstrips = 16
    else:
        numstrips = 1
    for strip in range(numstrips):
        df[detnames[det] + "_" + str(strip) + "_E"] = ecalE[det][strip] * df[detnames[det] + "_" + str(strip)]

Now, make a plot so we can check all of the energy calibration hists:

In [60]:
fig = px.histogram(df, x="D2_15_E", nbins=500)
fig.show()

We'll want to check how good our fits are by re-fitting all of the peaks and checking their centroids (to make sure they're all at 5.8 like we want).

In [55]:
for det in range(4):
    if det == 0 or det == 1:
        numstrips = 16
    else:
        numstrips = 1
    for strip in range(numstrips):
        cnts, binedges = np.histogram(df[detnames[det] + "_" + str(strip) + "_E"], 500, range=(0,10))
        
        binc = []
        for i in range(len(binedges)-1):
            binc.append((binedges[i]+binedges[i+1])/2)
            
        # For the height, use 80% of the highest bin, chopping off the first hundred bins, since the max should occur after:
        peaks, _ = find_peaks(cnts, height=np.amax(cnts[100:])*.3)
        if len(peaks) > 0:
            peak = peaks[len(peaks)-1]
            peakpos = binc[peak]
        else: peakpos = 0
        
        g_init = models.Gaussian1D(amplitude=5000, mean=peakpos, stddev=.2)
        fit_g = fitting.LevMarLSQFitter()
        g = fit_g(g_init, binc, cnts)
        
        print("Det: " + detnames[det] + " Strip: " + str(strip) + " Peak: " + str(g.mean.value) + " stddev: " + str(g.stddev.value))

Det: U2 Strip: 0 Peak: 5.811912082519575 stddev: 0.019686046066208312
Det: U2 Strip: 1 Peak: 5.806945570189796 stddev: 0.0125563882149041
Det: U2 Strip: 2 Peak: 5.797893949031594 stddev: 0.021565351863423534
Det: U2 Strip: 3 Peak: 5.799256212116298 stddev: 0.022603975844563695
Det: U2 Strip: 4 Peak: 5.805907215772462 stddev: 0.020922064590456382
Det: U2 Strip: 5 Peak: 5.811349747062112 stddev: 0.02278783191137622
Det: U2 Strip: 6 Peak: 5.8100807951979165 stddev: 0.02130444695705656
Det: U2 Strip: 7 Peak: 5.805790988551009 stddev: 0.026406435184872186
Det: U2 Strip: 8 Peak: 5.804005545346927 stddev: 0.01852299708137662
Det: U2 Strip: 9 Peak: 5.8084670345709135 stddev: 0.01180275821206282
Det: U2 Strip: 10 Peak: 5.800044568010845 stddev: 0.02207497964827194
Det: U2 Strip: 11 Peak: 5.79618611500629 stddev: 0.02299396299828503
Det: U2 Strip: 12 Peak: 5.8065826844181325 stddev: 0.01711553957431414
Det: U2 Strip: 13 Peak: 5.795618339702867 stddev: 0.01952871200228882
Det: U2 Strip: 14 Peak: 

Once all the calibrations above look good, we can go ahead and save the calibration array as a pickle to open later when we apply the calibration to the actual run files.

In [59]:
with open('Ecal.pkl', 'wb') as f:
    pickle.dump(ecalE, f)